In [3]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import os
import json
import glob
import numpy as np
import torch
import pandas as pd

from Server.model_lstm import LSTMRegressor

In [4]:
# ==================== 설정 ====================
ROUND = 1
ROUND_DIR = os.path.join("Rounds", f"round_{ROUND:04d}")
GLOBAL_JSON = os.path.join(ROUND_DIR, "global.json")
GLOBAL_PT = os.path.join(ROUND_DIR, "global.pt")
UPDATES_DIR = os.path.join(ROUND_DIR, "updates")
device = "cpu"

# CSV 경로
TEST_CSV = r"C:\Users\admin\OneDrive - 중앙대학교\Federated Learning\csv\Global Model Data.csv"
FEATURE_COLS = ["year"]
TARGET_COL = "chloride"

# ==================== 모델 로드 ====================
assert os.path.exists(GLOBAL_JSON), f"missing: {GLOBAL_JSON}"
assert os.path.exists(GLOBAL_PT), f"missing: {GLOBAL_PT}"

with open(GLOBAL_JSON, "r", encoding="utf-8") as f:
    meta = json.load(f)

cfg = meta["config"]
SEQ_LEN = cfg["seq_len"]

global_model = LSTMRegressor(
    input_size=cfg["input_size"],
    hidden_size=cfg["hidden_size"],
    num_layers=cfg["num_layers"],
    output_size=cfg["output_size"],
    dropout=cfg.get("dropout", 0.0),
).to(device)

global_sd = torch.load(GLOBAL_PT, map_location=device)
global_model.load_state_dict(global_sd, strict=True)

print(f"✓ Global model loaded from round {ROUND}")

# ==================== 클라이언트 업데이트 로드 ====================
def load_client_update(meta_path: str):
    with open(meta_path, "r", encoding="utf-8") as f:
        m = json.load(f)
    pt_path = m["weights_path"]
    if not os.path.exists(pt_path):
        raise FileNotFoundError(pt_path)
    sd = torch.load(pt_path, map_location=device)
    return m, sd

update_jsons = sorted(glob.glob(os.path.join(UPDATES_DIR, "client_*.json")))
client_updates = []
for mp in update_jsons:
    try:
        m, sd = load_client_update(mp)
        client_updates.append((m, sd))
    except Exception as e:
        print(f"⚠ Failed to load {mp}: {e}")

print(f"✓ Loaded {len(client_updates)} client updates")

# ==================== 클라이언트 파라미터 평균 로드 ====================
AGG_JSON = os.path.join(ROUND_DIR, "aggregated.json")
AGG_PT   = os.path.join(ROUND_DIR, "aggregated.pt")

assert os.path.exists(AGG_JSON), f"missing: {AGG_JSON}"
assert os.path.exists(AGG_PT),   f"missing: {AGG_PT}"

with open(AGG_JSON, "r", encoding="utf-8") as f:
    agg_meta = json.load(f)

aggregated_sd = torch.load(AGG_PT, map_location="cpu")

✓ Global model loaded from round 1
✓ Loaded 2 client updates


In [5]:
# ==================== 유틸리티 함수 ====================
def state_dict_diff_stats(base_sd: dict, new_sd: dict):
    keys = list(base_sd.keys())
    per_key = []
    total_sq = 0.0
    total_n = 0

    for k in keys:
        b = base_sd[k].detach().cpu().float()
        n = new_sd[k].detach().cpu().float()
        d = (n - b).reshape(-1)
        sq = float((d*d).sum().item())
        nn = d.numel()
        total_sq += sq
        total_n += nn

        per_key.append({
            "key": k,
            "l2": float(np.sqrt(sq)),
            "rmse": float(np.sqrt(sq / max(nn, 1))),
            "max_abs": float(d.abs().max().item()) if nn > 0 else 0.0,
            "numel": nn
        })

    total_l2 = float(np.sqrt(total_sq))
    total_rmse = float(np.sqrt(total_sq / max(total_n, 1)))
    per_key_sorted = sorted(per_key, key=lambda x: x["l2"], reverse=True)

    return {
        "total_l2": total_l2,
        "total_rmse": total_rmse,
        "per_key_sorted": per_key_sorted
    }

def flatten_params(sd: dict):
    arrs = []
    for k, v in sd.items():
        arrs.append(v.detach().cpu().float().reshape(-1))
    return torch.cat(arrs).numpy()

def make_windows(features, targets, seq_len):
    if targets.ndim == 1:
        targets = targets.reshape(-1, 1)
    N, F = features.shape
    M = N - seq_len
    if M <= 0:
        raise ValueError(f"Not enough rows: N={N}, seq_len={seq_len}")
    X = np.zeros((M, seq_len, F), dtype=np.float32)
    y = np.zeros((M, 1), dtype=np.float32)
    for i in range(M):
        X[i] = features[i:i+seq_len]
        y[i] = targets[i+seq_len]
    return X, y


In [6]:
# ==================== 1. 클라이언트별 파라미터 변화 요약 ====================
summaries = []
for meta_c, sd_c in client_updates:
    stats = state_dict_diff_stats(global_sd, sd_c)
    summaries.append({
        "client_id": meta_c["client_id"],
        "n_samples": meta_c["n_samples"],
        "local_loss": meta_c.get("local_loss", None),
        "total_l2": stats["total_l2"],
        "total_rmse": stats["total_rmse"],
    })

if summaries:
    df_summary = pd.DataFrame(summaries)
    
    # 시각화 1: 클라이언트별 L2 거리
    fig1 = go.Figure()
    fig1.add_trace(go.Bar(
        x=[s["client_id"] for s in summaries],
        y=[s["total_l2"] for s in summaries],
        marker=dict(color=[s["n_samples"] for s in summaries], 
                    colorscale="Viridis", 
                    showscale=True,
                    colorbar=dict(title="N samples")),
        text=[f"Loss: {s['local_loss']:.4f}" if s['local_loss'] else "" for s in summaries],
        textposition="outside"
    ))
    fig1.update_layout(
        title=f"Client Parameter Updates (Round {ROUND})",
        xaxis_title="Client ID",
        yaxis_title="Total L2 Distance from Global",
        template="plotly_white",
        height=500
    )
    fig1.show()


In [7]:
def flatten_params(sd: dict):
    arrs = []
    for k, v in sd.items():
        arrs.append(v.detach().cpu().float().reshape(-1))
    return torch.cat(arrs).numpy()

global_vec = np.asarray(flatten_params(global_sd), dtype=np.float64)
agg_vec    = np.asarray(flatten_params(aggregated_sd), dtype=np.float64)

client_vecs = []
client_ids  = []

for m, sd in client_updates:
    cid = int(m["client_id"])
    v = np.asarray(flatten_params(sd), dtype=np.float64)

    # 혹시 길이가 다르면(모델 구조가 다른 경우) 제외하는 게 안전
    if len(v) != len(global_vec):
        print(f"[skip] client {cid}: param length mismatch ({len(v)} != {len(global_vec)})")
        continue

    client_ids.append(cid)
    client_vecs.append(v)

if len(client_vecs) == 0:
    raise RuntimeError("No valid client updates found")

print("clients:", client_ids)

# numpy float64로 통일
global_vec = np.asarray(global_vec, dtype=np.float64)
client_vec = np.asarray(client_vecs, dtype=np.float64)
agg_vec    = np.asarray(agg_vec, dtype=np.float64)

fig = go.Figure()

# 각 클라이언트 변화량 분포
for cid, v in zip(client_ids, client_vecs):
    diff = v - global_vec
    fig.add_trace(go.Histogram(
        x=diff,
        nbinsx=80,
        histnorm="probability density",
        name=f"Client {cid} − Global",
        opacity=0.35
    ))

# 집계 변화량(연합 결과)
diff_agg = agg_vec - global_vec
fig.add_trace(go.Histogram(
    x=diff_agg,
    nbinsx=80,
    histnorm="probability density",
    name="Aggregated − Global",
    opacity=0.7
))

fig.update_layout(
    title="Update distribution comparison (Δw = model − global)",
    xaxis_title="Parameter difference (Δw)",
    yaxis_title="Density",
    template="plotly_white",
    barmode="overlay",
    height=450
)

fig.show()



clients: [1, 2]


In [8]:
# ==================== 2. 파라미터 분포 비교 (모든 클라이언트) ====================
if client_updates:
    global_vec = flatten_params(global_sd)
    
    # 모든 클라이언트의 파라미터 분포를 하나의 그래프에
    fig2 = go.Figure()
    
    # Global 분포 추가
    fig2.add_trace(go.Histogram(
        x=global_vec,
        nbinsx=60,
        name="Global Model",
        opacity=0.7,
        marker_color="black"
    ))
    
    # 각 클라이언트 분포 추가
    colors = ["steelblue", "coral", "mediumseagreen", "mediumpurple", "orange", "pink"]
    for idx, (meta_c, sd_c) in enumerate(client_updates):
        client_vec = flatten_params(sd_c)
        fig2.add_trace(go.Histogram(
            x=client_vec,
            nbinsx=60,
            name=f"Client {meta_c['client_id']}",
            opacity=0.5,
            marker_color=colors[idx % len(colors)]
        ))
    
    fig2.update_layout(
        title=f"Parameter Distribution - All Clients (Round {ROUND})",
        xaxis_title="Parameter Value",
        yaxis_title="Count",
        barmode="overlay",
        template="plotly_white",
        height=500,
        legend=dict(x=1.05, y=1)
    )
    fig2.show()
    
    # 차이 분포 비교 (각 클라이언트 - Global)
    fig2_diff = go.Figure()
    
    for idx, (meta_c, sd_c) in enumerate(client_updates):
        client_vec = flatten_params(sd_c)
        diff_vec = client_vec - global_vec
        
        fig2_diff.add_trace(go.Histogram(
            x=diff_vec,
            nbinsx=60,
            name=f"Client {meta_c['client_id']} - Global",
            opacity=0.6,
            marker_color=colors[idx % len(colors)]
        ))
    
    fig2_diff.update_layout(
        title=f"Parameter Difference Distribution (Round {ROUND})",
        xaxis_title="Parameter Change",
        yaxis_title="Count",
        barmode="overlay",
        template="plotly_white",
        height=500,
        legend=dict(x=1.05, y=1)
    )
    fig2_diff.show()

In [9]:
# ==================== 3. 레이어별 변화량 (모든 클라이언트) ====================
if client_updates:
    # 각 클라이언트별로 subplot 생성
    n_clients = len(client_updates)
    fig3 = make_subplots(
        rows=1, cols=n_clients,
        subplot_titles=[f"Client {m['client_id']}" for m, _ in client_updates],
        horizontal_spacing=0.15
    )
    
    for idx, (meta_c, sd_c) in enumerate(client_updates):
        stats = state_dict_diff_stats(global_sd, sd_c)
        top = stats["per_key_sorted"][:10]  # Top 10으로 줄임
        
        fig3.add_trace(
            go.Bar(
                y=[t["key"].split('.')[-1] for t in top][::-1],  # 레이어 이름 축약
                x=[t["l2"] for t in top][::-1],
                orientation='h',
                marker=dict(
                    color=[t["l2"] for t in top][::-1],
                    colorscale="YlOrRd",
                    showscale=(idx == n_clients - 1)  # 마지막에만 colorbar 표시
                ),
                showlegend=False,
                hovertext=[t["key"] for t in top][::-1],  # hover에 전체 이름 표시
                hovertemplate="<b>%{hovertext}</b><br>L2: %{x:.2e}<extra></extra>"
            ),
            row=1, col=idx+1
        )
    
    fig3.update_layout(
        title_text=f"Top 10 Layer Changes per Client (Round {ROUND})",
        template="plotly_white",
        height=500
    )
    fig3.update_xaxes(title_text="L2 Norm")
    fig3.show()
    
    # 전체 클라이언트 레이어별 변화량 히트맵
    all_keys = list(global_sd.keys())
    client_ids = [m["client_id"] for m, _ in client_updates]
    heatmap_data = []
    
    for key in all_keys:
        row = []
        for _, sd_c in client_updates:
            b = global_sd[key].detach().cpu().float().reshape(-1)
            c = sd_c[key].detach().cpu().float().reshape(-1)
            l2 = float(torch.sqrt(((c - b) ** 2).sum()).item())
            row.append(l2)
        heatmap_data.append(row)
    
    fig3_heat = go.Figure(data=go.Heatmap(
        z=heatmap_data,
        x=client_ids,
        y=[k.split('.')[-1] for k in all_keys],  # 레이어 이름 축약
        colorscale="YlOrRd",
        hovertext=all_keys,  # hover에 전체 이름
        hovertemplate="<b>%{hovertext}</b><br>Client: %{x}<br>L2: %{z:.2e}<extra></extra>"
    ))
    
    fig3_heat.update_layout(
        title=f"Layer-wise Change Heatmap (Round {ROUND})",
        xaxis_title="Client ID",
        yaxis_title="Layer",
        template="plotly_white",
        height=600
    )
    fig3_heat.show()

In [10]:
# ==================== 4. 예측 비교 (모든 클라이언트) ====================
df = pd.read_csv(TEST_CSV)
df = df.dropna(subset=FEATURE_COLS + [TARGET_COL]).reset_index(drop=True)

features = df[FEATURE_COLS].to_numpy(dtype=np.float32)
targets = df[TARGET_COL].to_numpy(dtype=np.float32)

X, y = make_windows(features, targets, seq_len=SEQ_LEN)
X_t = torch.from_numpy(X).to(device)

global_model.eval()
with torch.no_grad():
    pred_global = global_model(X_t).detach().cpu().numpy().reshape(-1)

y_true = y.reshape(-1)

fig4 = go.Figure()

# Ground Truth
fig4.add_trace(go.Scatter(
    x=np.arange(len(y_true)),
    y=y_true,
    mode="lines",
    name="Ground Truth",
    line=dict(color="black", width=2.5)
))

# Global Model
fig4.add_trace(go.Scatter(
    x=np.arange(len(pred_global)),
    y=pred_global,
    mode="lines",
    name="Global Model",
    line=dict(color="red", width=2, dash="dash")
))

# 모든 클라이언트 모델
colors = ["steelblue", "coral", "mediumseagreen", "mediumpurple", "orange", "pink"]
for idx, (meta_c, sd_c) in enumerate(client_updates):
    client_model = LSTMRegressor(
        input_size=cfg["input_size"],
        hidden_size=cfg["hidden_size"],
        num_layers=cfg["num_layers"],
        output_size=cfg["output_size"],
        dropout=cfg.get("dropout", 0.0),
    ).to(device)
    client_model.load_state_dict(sd_c, strict=True)
    client_model.eval()
    
    with torch.no_grad():
        pred_client = client_model(X_t).detach().cpu().numpy().reshape(-1)
    
    fig4.add_trace(go.Scatter(
        x=np.arange(len(pred_client)),
        y=pred_client,
        mode="lines",
        name=f"Client {meta_c['client_id']}",
        line=dict(color=colors[idx % len(colors)], width=1.5, dash="dot"),
        opacity=0.8
    ))

fig4.update_layout(
    title="Model Prediction Comparison - All Clients",
    xaxis_title="Time Index",
    yaxis_title="Chloride",
    template="plotly_white",
    height=550,
    hovermode="x unified",
    legend=dict(x=1.05, y=1)
)
fig4.show()

# MSE 비교 바 차트
mse_data = []
mse_data.append({
    "model": "Global",
    "mse": float(np.mean((y_true - pred_global) ** 2))
})

for meta_c, sd_c in client_updates:
    client_model = LSTMRegressor(
        input_size=cfg["input_size"],
        hidden_size=cfg["hidden_size"],
        num_layers=cfg["num_layers"],
        output_size=cfg["output_size"],
        dropout=cfg.get("dropout", 0.0),
    ).to(device)
    client_model.load_state_dict(sd_c, strict=True)
    client_model.eval()
    
    with torch.no_grad():
        pred_client = client_model(X_t).detach().cpu().numpy().reshape(-1)
    
    mse_data.append({
        "model": f"Client {meta_c['client_id']}",
        "mse": float(np.mean((y_true - pred_client) ** 2))
    })

fig4_mse = go.Figure()
fig4_mse.add_trace(go.Bar(
    x=[d["model"] for d in mse_data],
    y=[d["mse"] for d in mse_data],
    marker=dict(color=["red"] + colors[:len(client_updates)]),
    text=[f"{d['mse']:.4f}" for d in mse_data],
    textposition="outside"
))

fig4_mse.update_layout(
    title="Mean Squared Error Comparison",
    xaxis_title="Model",
    yaxis_title="MSE",
    template="plotly_white",
    height=450
)
fig4_mse.show()

In [11]:
# ==================== 5. Global Model 파라미터 체크 ====================
print("\n" + "="*60)
print("GLOBAL MODEL PARAMETER SUMMARY")
print("="*60)

total_params = 0
for name, p in global_model.named_parameters():
    mean = p.data.mean().item()
    std = p.data.std().item()
    shape_str = str(tuple(p.shape))
    print(f"{name:35s} | shape={shape_str:20s} | mean={mean:+.4e} | std={std:+.4e}")
    total_params += p.numel()

print(f"\nTotal parameters: {total_params:,}")


GLOBAL MODEL PARAMETER SUMMARY
lstm.weight_ih_l0                   | shape=(256, 1)             | mean=+1.5403e-03 | std=+7.1630e-02
lstm.weight_hh_l0                   | shape=(256, 64)            | mean=+1.6712e-05 | std=+7.5872e-02
lstm.bias_ih_l0                     | shape=(256,)               | mean=-6.1333e-03 | std=+7.2941e-02
lstm.bias_hh_l0                     | shape=(256,)               | mean=-5.9096e-03 | std=+7.4014e-02
fc.weight                           | shape=(1, 64)              | mean=-1.6025e-03 | std=+6.7883e-02
fc.bias                             | shape=(1,)                 | mean=+7.2429e-02 | std=+nan

Total parameters: 17,217


C:\Users\admin\AppData\Local\Temp\ipykernel_32108\1582688639.py:9: UserWarning:

std(): degrees of freedom is <= 0. Correction should be strictly less than the reduction factor (input numel divided by output numel). (Triggered internally at C:\actions-runner\_work\pytorch\pytorch\pytorch\aten\src\ATen\native\ReduceOps.cpp:1831.)



In [12]:
# ==================== 6. 전체 파라미터 분포 ====================
def plot_weight_hist_all(model, max_points=200_000, bins=80, title="Weight Distribution"):
    vec = torch.cat([p.detach().cpu().float().reshape(-1) for p in model.parameters()])
    n = vec.numel()
    
    if n > max_points:
        idx = torch.randperm(n)[:max_points]
        v = vec[idx].numpy()
        subtitle = f"Sampled {max_points:,} / {n:,}"
    else:
        v = vec.numpy()
        subtitle = f"All {n:,} parameters"
    
    fig = go.Figure()
    fig.add_trace(go.Histogram(
        x=v,
        nbinsx=bins,
        marker=dict(color="steelblue", line=dict(color="white", width=0.5))
    ))
    fig.update_layout(
        title=f"{title}<br><sub>{subtitle}</sub>",
        xaxis_title="Parameter Value",
        yaxis_title="Count",
        template="plotly_white",
        height=450
    )
    fig.show()

plot_weight_hist_all(global_model, title=f"Global Model Weight Distribution (Round {ROUND})")

In [13]:
# ==================== 7. Year vs Chloride 예측 ====================
years = df["year"].values.astype(np.float32)
chloride_true = df["chloride"].values.astype(np.float32)

X_full = []
for i in range(len(years) - SEQ_LEN):
    X_full.append(years[i:i+SEQ_LEN])

X_full = torch.tensor(X_full).unsqueeze(-1)

global_model.eval()
with torch.no_grad():
    y_pred = global_model(X_full).cpu().numpy().flatten()

x_plot = years[SEQ_LEN:]

fig5 = go.Figure()
fig5.add_trace(go.Scatter(
    x=years,
    y=chloride_true,
    mode="markers",
    name="Observed Data",
    marker=dict(color="black", size=8, symbol="circle")
))
fig5.add_trace(go.Scatter(
    x=x_plot,
    y=y_pred,
    mode="lines",
    name="Global Model Prediction",
    line=dict(color="red", width=3)
))

fig5.update_layout(
    title="Global LSTM Prediction: Year vs Chloride",
    xaxis_title="Year",
    yaxis_title="Chloride",
    template="plotly_white",
    height=500,
    hovermode="x unified"
)
fig5.show()


C:\Users\admin\AppData\Local\Temp\ipykernel_32108\2815329184.py:9: UserWarning:

Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at C:\actions-runner\_work\pytorch\pytorch\pytorch\torch\csrc\utils\tensor_new.cpp:257.)



In [14]:
# ==================== 8. 라운드별 텐서 변화 추적 ====================
TENSOR = "lstm.weight_hh_l0"
ROUNDS = [1, 2, 3]  # 존재하는 라운드만 자동으로 로드됨

fig6 = go.Figure()
loaded = 0

for r in ROUNDS:
    rdir = os.path.join("Rounds", f"round_{r:04d}")
    gpt = os.path.join(rdir, "global.pt")
    if not os.path.exists(gpt):
        continue
    
    sd = torch.load(gpt, map_location="cpu")
    if TENSOR not in sd:
        continue
    
    v = sd[TENSOR].detach().cpu().float().reshape(-1).numpy()
    
    fig6.add_trace(go.Histogram(
        x=v,
        nbinsx=80,
        name=f"Round {r}",
        opacity=0.6
    ))
    loaded += 1

if loaded > 0:
    fig6.update_layout(
        title=f"Tensor Distribution Across Rounds: {TENSOR}",
        xaxis_title="Parameter Value",
        yaxis_title="Count",
        barmode="overlay",
        template="plotly_white",
        height=500
    )
    fig6.show()
else:
    print(f"⚠ No data loaded for tensor {TENSOR} across rounds {ROUNDS}")

In [15]:
# ==================== 9. 라운드별 통계 테이블 ====================
rows = []
for r in ROUNDS:
    rdir = os.path.join("Rounds", f"round_{r:04d}")
    gpt = os.path.join(rdir, "global.pt")
    if not os.path.exists(gpt):
        continue
    sd = torch.load(gpt, map_location="cpu")
    if TENSOR not in sd:
        continue
    v = sd[TENSOR].detach().cpu().float().reshape(-1).numpy()
    rows.append({
        "round": r,
        "n": v.size,
        "mean": float(v.mean()),
        "std": float(v.std()),
        "min": float(v.min()),
        "max": float(v.max()),
        "p01": float(np.quantile(v, 0.01)),
        "p99": float(np.quantile(v, 0.99)),
    })

if rows:
    df_stats = pd.DataFrame(rows).sort_values("round")
    print("\n" + "="*60)
    print(f"TENSOR STATISTICS: {TENSOR}")
    print("="*60)
    print(df_stats.to_string(index=False))


TENSOR STATISTICS: lstm.weight_hh_l0
 round     n      mean      std       min      max       p01      p99
     1 16384  0.000017 0.075870 -0.190784 0.191599 -0.142007 0.142245
     2 16384 -0.000193 0.075853 -0.179436 0.184759 -0.142179 0.143788


In [16]:
# ==================== 10. 라운드 간 예측 비교 ====================
def load_model(round_id):
    rdir = os.path.join("Rounds", f"round_{round_id:04d}")
    json_path = os.path.join(rdir, "global.json")
    pt_path = os.path.join(rdir, "global.pt")
    
    with open(json_path, "r", encoding="utf-8") as f:
        meta = json.load(f)
    
    cfg = meta["config"]
    model = LSTMRegressor(
        input_size=cfg["input_size"],
        hidden_size=cfg["hidden_size"],
        num_layers=cfg["num_layers"],
        output_size=cfg["output_size"],
        dropout=cfg.get("dropout", 0.0),
    ).to(device)
    
    model.load_state_dict(torch.load(pt_path, map_location=device))
    model.eval()
    return model

# 여러 라운드 비교
compare_rounds = [1, 2, 3]
fig7 = go.Figure()

# Ground truth
fig7.add_trace(go.Scatter(
    x=np.arange(len(y.flatten())),
    y=y.flatten(),
    mode="lines",
    name="Ground Truth",
    line=dict(color="black", width=3)
))

colors = ["steelblue", "coral", "mediumseagreen", "mediumpurple"]
for idx, r in enumerate(compare_rounds):
    try:
        model_r = load_model(r)
        with torch.no_grad():
            pred_r = model_r(X_t).squeeze().cpu().numpy().flatten()
        
        fig7.add_trace(go.Scatter(
            x=np.arange(len(pred_r)),
            y=pred_r,
            mode="lines",
            name=f"Round {r}",
            line=dict(color=colors[idx % len(colors)], width=2, dash="dash")
        ))
    except Exception as e:
        print(f"⚠ Could not load round {r}: {e}")

fig7.update_layout(
    title="Multi-Round Prediction Comparison",
    xaxis_title="Time Index",
    yaxis_title="Chloride",
    template="plotly_white",
    height=550,
    hovermode="x unified"
)
fig7.show()

print("\n" + "="*60)
print("✓ All visualizations complete!")
print("="*60)

⚠ Could not load round 3: [Errno 2] No such file or directory: 'Rounds\\round_0003\\global.json'



✓ All visualizations complete!
